<h1 align=center><font size = 7> A tailored neighborhood in New York City</font></h1>

# 1. Introduction

## 1.1 Problem

We want to create a score for neighborhoods in New York so that professionals that work in Manhattan can easily find the most suitable option for them.  
The variables we are interested in are the distance from Manhattan, the median rent cost and the neighborhood venues profile.

## 1.2 Analysis 

Neighborhoods are complex systems and many different variables are at play.  
For our analysis we will focus on median rent price, distance from Manhattan and the kind of venues present around the area.  
We will start by segmenting neighborhoods on the base of their venues profile.  
We want to create many different profiles so that they could more closely relate to the many different interests people might have.  
We will have to create some kind of weighting system to balance the variables of distance from Manahattan (giving a better score to those in Manhattan or closer) and median cost of rent.  
The distance from Manhattan will be calculated as 0 for the neighborhoods in the Borough of Manahattan and as the distance from the closest neighborhood in Manhattan Borough for all the others and we will probably have to normalize it.  
After these stesps we should be able to create a scoring system so that we can rank each neaighborhood in their respective category.

# 2. Methodology 

## 2.1 Data sources

* Data for the geography median rent cost (we will use the data for 2BR apartments as a reference) by neighborhood will be gathered from the website renthop.com (https://www.renthop.com/study/assets/new-york-city-cost-of-living-2017/nyc_col_geojson.js) which is a GeoJson that also contains our rent info.  
* The venues data will be retrieved from FourSquare.com using the API provided.  

## 2.2 Data retrieval 

### 2.2.1 Import and install necessary libraries

Proceding with the necessary import

In [407]:
# uncomment the following line if geopy isn't installed
#!conda install -c conda-forge geopy --yes 

# uncomment the following line if folium isn't installed
!conda install -c conda-forge folium=0.5.0 --yes 


# install BeautifulSoup and requests
#!pip install beautifulsoup4
!pip install requests
!pip install lxml

import re

# library to handle data in a vectorized manner
import numpy as np 

# library for data analsysis
import pandas as pd 
from pandas import json_normalize # tranform JSON file into a pandas dataframe

# import BeautifulSoup
#from bs4 import BeautifulSoup

# library to handle JSON files
import json

# convert an address into latitude and longitude values
from geopy.geocoders import Nominatim 

# library to handle http requests
import requests 

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

# map rendering library
import folium 

print('Libraries imported.')

Solving environment: ...working... 
  - anaconda/win-64::ca-certificates-2020.1.1-0, anaconda/win-64::certifi-2019.11.28-py37_0, anaconda/win-64::openssl-1.1.1d-he774522_4
  - anaconda/win-64::ca-certificates-2020.1.1-0, anaconda/win-64::certifi-2019.11.28-py37_0, defaults/win-64::openssl-1.1.1d-he774522_4
  - anaconda/win-64::certifi-2019.11.28-py37_0, anaconda/win-64::openssl-1.1.1d-he774522_4, defaults/win-64::ca-certificates-2020.1.1-0
  - anaconda/win-64::certifi-2019.11.28-py37_0, defaults/win-64::ca-certificates-2020.1.1-0, defaults/win-64::openssl-1.1.1d-he774522_4
  - anaconda/win-64::openssl-1.1.1d-he774522_4, defaults/win-64::ca-certificates-2020.1.1-0, defaults/win-64::certifi-2019.11.28-py37_0
  - defaults/win-64::ca-certificates-2020.1.1-0, defaults/win-64::certifi-2019.11.28-py37_0, defaults/win-64::openssl-1.1.1d-he774522_4
  - anaconda/win-64::ca-certificates-2020.1.1-0, anaconda/win-64::openssl-1.1.1d-he774522_4, defaults/win-64::certifi-2019.11.28-py37_0
  - anaconda

### 2.2.2 NYC Neighborhoods rent and geography data

Let's proceed with the download of the dataset of New York Neighborhoods Geography which comes as a GeoJson file.

In [408]:
url = 'https://www.renthop.com/study/assets/new-york-city-cost-of-living-2017/nyc_col_geojson.js'
filename = 'newyork_rent_location_data.json'
response = requests.get(url)
file = open(filename, "w")
file.write(re.sub(r'var shapes.*?{', '{', response.text))
with open(filename) as json_rent_location_data:
    newyork_rent_location_data = json.load(json_rent_location_data)
newyork_rent_location_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-74.000959, 40.694069],
       [-74.003014, 40.694778],
       [-74.002398, 40.695712],
       [-74.000269, 40.694966],
       [-74.000959, 40.694069]]],
     [[[-73.999474, 40.696704],
       [-73.999524, 40.696575],
       [-74.000489, 40.696926],
       [-74.000431, 40.697052],
       [-73.999593, 40.696782],
       [-73.999554, 40.696945],
       [-73.999407, 40.696885],
       [-73.999474, 40.696704]]],
     [[[-73.998378, 40.698063],
       [-73.998871, 40.697158],
       [-74.001049, 40.697908],
       [-74.000488, 40.698758],
       [-73.998378, 40.698063]]],
     [[[-73.998021, 40.698762],
       [-74.000018, 40.699466],
       [-73.999475, 40.700323],
       [-73.997499, 40.699639],
       [-73.998021, 40.698762]]],
     [[[-73.996698, 40.700877],
       [-73.996822, 40.700991],
       [-73.99776, 40.701359],
       [-73.997802, 40.701319],
       [-7

### 2.2.2 Data cleansing

Analyzing the content we can notice many information are available in this set, for the sake of this study from this josn we need to retrieve the Borough and Neighborhood name along with it's geography.  
These informations are available in each feature instance through  __features.properties.Neighborhood__, __features.properties.Borough__, __features.properties.median2__ and __features.geometry__ contain all the informations needed to define the neighborhood area.  
Let's use the json_normalize method to transfer the information into a DataFrame and we will decide which informations are worth keeping later.

In [409]:
neighborhoods_rent_location_data = newyork_rent_location_data['features']

neighborhoods_rent_location = json_normalize(neighborhoods_rent_location_data)
neighborhoods_rent_location

type geometry.type                               geometry.coordinates  \
0    Feature  MultiPolygon  [[[[-74.000959, 40.694069], [-74.003014, 40.69...   
1    Feature       Polygon  [[[-73.96003, 40.798038], [-73.974997, 40.7775...   
2    Feature       Polygon  [[[-73.982556, 40.73135], [-73.978027, 40.7294...   
3    Feature       Polygon  [[[-73.993831, 40.772932], [-73.993503, 40.772...   
4    Feature  MultiPolygon  [[[[-73.962304, 40.733114], [-73.962263, 40.73...   
..       ...           ...                                                ...   
190  Feature  MultiPolygon  [[[[-73.746994, 40.637151], [-73.747, 40.63712...   
191  Feature       Polygon  [[[-74.169826, 40.56109], [-74.169775, 40.5603...   
192  Feature  MultiPolygon  [[[[-74.159456, 40.641448], [-74.159979, 40.64...   
193  Feature       Polygon  [[[-73.760315, 40.67511], [-73.758572, 40.6726...   
194  Feature       Polygon  [[[-73.872872, 40.785975], [-73.872885, 40.785...   

    properties.ntacode                            properties.Neighborhood  \
0                 MN25                  Battery Park City-Lower Manhattan   
1                 MN12                                    Upper West Side   
2                 MN22                                       East Village   
3                 MN15                                            Clinton   
4                 MN20                               Murray Hill-Kips Bay   
..                 ...                                                ...   
190               QN98                                            Airport   
191               SI01         Annadale-Huguenot-Prince's Bay-Eltingville   
192               SI12  Mariner's Harbor-Arlington-Port Ivory-Granitev...   
193               QN02                          Springfield Gardens North   
194               BX98                                      Rikers Island   

    properties.Borough  properties.house_income  properties.median2  \
0            Manhattan                 125434.0              4552.5   
1            Manhattan                  92268.0              3980.0   
2            Manhattan                  72665.0              3750.0   
3            Manhattan                  73591.0              3600.0   
4            Manhattan                  97458.0              3498.0   
..                 ...                      ...                 ...   
190             Queens                      NaN                 NaN   
191      Staten Island                      NaN                 NaN   
192      Staten Island                      NaN                 NaN   
193             Queens                      NaN                 NaN   
194              Bronx                      NaN                 NaN   

     properties.perc_income  properties.income4_2Br  
0                  0.435528                182100.0  
1                  0.517623                159200.0  
2                  0.619280                150000.0  
3                  0.587028                144000.0  
4                  0.430709                139920.0  
..                      ...                     ...  
190                     NaN                     NaN  
191                     NaN                     NaN  
192                     NaN                     NaN  
193                     NaN                     NaN  
194                     NaN                     NaN  

[195 rows x 10 columns]

'type', 'properties.ntacode', 'properties.house_income', 'properties.perc_income', 'properties.income4_2Br' have no use for us so we can just drop them.  
Regarding 'geometry.coordinates' and 'geometry.type' might be useful in later stages so we will keep it. We can also fix other columns names and reorder them.

In [410]:
neighborhoods_data = neighborhoods_rent_location.drop(['type', 'properties.ntacode', 'properties.house_income', 'properties.perc_income', 'properties.income4_2Br'], axis = 1).rename(columns = {'properties.Neighborhood':'Neighborhood', 'properties.Borough':'Borough', 'properties.median2':'Median rent'})
neighborhoods_data = neighborhoods_data[['Borough','Neighborhood','Median rent','geometry.coordinates', 'geometry.type']]
neighborhoods_data.head()

Borough                       Neighborhood  Median rent  \
0  Manhattan  Battery Park City-Lower Manhattan       4552.5   
1  Manhattan                    Upper West Side       3980.0   
2  Manhattan                       East Village       3750.0   
3  Manhattan                            Clinton       3600.0   
4  Manhattan               Murray Hill-Kips Bay       3498.0   

                                geometry.coordinates geometry.type  
0  [[[[-74.000959, 40.694069], [-74.003014, 40.69...  MultiPolygon  
1  [[[-73.96003, 40.798038], [-73.974997, 40.7775...       Polygon  
2  [[[-73.982556, 40.73135], [-73.978027, 40.7294...       Polygon  
3  [[[-73.993831, 40.772932], [-73.993503, 40.772...       Polygon  
4  [[[[-73.962304, 40.733114], [-73.962263, 40.73...  MultiPolygon

To better navigate the Frame we can set a multi index on Borough and Neighborhood.

In [411]:
neighborhoods_data = neighborhoods_data.sort_values(by = ['Borough','Neighborhood']).set_index(['Borough','Neighborhood'])
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                              
Bronx   Allerton-Pelham Gardens             NaN   
        Bedford Park-Fordham North       1895.0   
        Belmont                             NaN   
        Bronxdale                           NaN   
        Claremont-Bathgate                  NaN   

                                                                 geometry.coordinates  \
Borough Neighborhood                                                                    
Bronx   Allerton-Pelham Gardens     [[[-73.853636, 40.873301], [-73.848597, 40.871...   
        Bedford Park-Fordham North  [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        Belmont                     [[[-73.883094, 40.866602], [-73.882676, 40.866...   
        Bronxdale                   [[[-73.861379, 40.871337], [-73.861563, 40.865...   
        Claremont-Bathgate          [[[-73.89039, 40.854689], [-73.892167, 40.8527...   

                                   geometry.type  
Borough Neighborhood                              
Bronx   Allerton-Pelham Gardens          Polygon  
        Bedford Park-Fordham North       Polygon  
        Belmont                          Polygon  
        Bronxdale                        Polygon  
        Claremont-Bathgate               Polygon

In [412]:
neighborhoods_data['Median rent'].isnull().sum()

56

As we can see some neighborhoods do not have rent data and try to find other sources for this information would lead to a mistmatch in results due to many different factor such as a different period in time were the survey has been conducted, different kind of houses (not only 2BR as we are considering here) different neighborhoods definition and so on.
The only sensible choice here is, unfortunately, to drop those rows.

In [413]:
neighborhoods_data.dropna(subset = ['Median rent'], inplace = True)
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             1895.0   
        East Concourse-Concourse Village       2225.0   
        Highbridge                             2008.0   
        Hunts Point                            1937.5   
        Melrose South-Mott Haven North         1875.0   

                                                                       geometry.coordinates  \
Borough Neighborhood                                                                          
Bronx   Bedford Park-Fordham North        [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        East Concourse-Concourse Village  [[[-73.909587, 40.842756], [-73.909625, 40.842...   
        Highbridge                        [[[-73.917287, 40.845104], [-73.917507, 40.844...   
        Hunts Point                       [[[-73.88439, 40.822967], [-73.883788, 40.8219...   
        Melrose South-Mott Haven North    [[[-73.901293, 40.820475], [-73.90301, 40.8163...   

                                         geometry.type  
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             Polygon  
        East Concourse-Concourse Village       Polygon  
        Highbridge                             Polygon  
        Hunts Point                            Polygon  
        Melrose South-Mott Haven North         Polygon

### 2.2.3 Defining a Neighborhood center

We are now gonna need to find a center for our neighborhoods to get the venues in the area and to calculate the distance from Manhattan. 

#### 2.2.3.1 Centroid from all points avarage 

We can easily calculate the centroid of the area using a pandas mean.

In [414]:
for index, row in neighborhoods_data.iterrows():
    if row[2] == 'Polygon':
        df = pd.DataFrame(row[1]).T
        count = 0
        latitude_avg = 0
        longitude_avg = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.dropna().tolist())
            longitude_avg += df2.mean()[0]
            latitude_avg += df2.mean()[1]
            count += 1
    elif row[2] == 'MultiPolygon':
        df = pd.DataFrame(row[1])
        count = 0
        latitude_avg = 0
        longitude_avg = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.tolist()).T
            for index3, column3 in df2.iteritems():
                df3 = pd.DataFrame(column3.dropna().tolist())
                longitude_avg += df3.mean()[0]
                latitude_avg += df3.mean()[1]
                count += 1
    neighborhoods_data.loc[index, 'latitude_avg']= latitude_avg/count
    neighborhoods_data.loc[index, 'longitude_avg']= longitude_avg/count
    
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             1895.0   
        East Concourse-Concourse Village       2225.0   
        Highbridge                             2008.0   
        Hunts Point                            1937.5   
        Melrose South-Mott Haven North         1875.0   

                                                                       geometry.coordinates  \
Borough Neighborhood                                                                          
Bronx   Bedford Park-Fordham North        [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        East Concourse-Concourse Village  [[[-73.909587, 40.842756], [-73.909625, 40.842...   
        Highbridge                        [[[-73.917287, 40.845104], [-73.917507, 40.844...   
        Hunts Point                       [[[-73.88439, 40.822967], [-73.883788, 40.8219...   
        Melrose South-Mott Haven North    [[[-73.901293, 40.820475], [-73.90301, 40.8163...   

                                         geometry.type  latitude_avg  \
Borough Neighborhood                                                   
Bronx   Bedford Park-Fordham North             Polygon     40.867928   
        East Concourse-Concourse Village       Polygon     40.831691   
        Highbridge                             Polygon     40.838775   
        Hunts Point                            Polygon     40.807513   
        Melrose South-Mott Haven North         Polygon     40.818142   

                                          longitude_avg  
Borough Neighborhood                                     
Bronx   Bedford Park-Fordham North           -73.890009  
        East Concourse-Concourse Village     -73.914419  
        Highbridge                           -73.926395  
        Hunts Point                          -73.886837  
        Melrose South-Mott Haven North       -73.916419

In [415]:
means = neighborhoods_data.mean()
lat = means[1]
lon = means[2]

In [416]:
open(filename)
# create a plain world map
ny_map1 = folium.Map(location=[lat, lon], zoom_start=10)
ny_map_mix = folium.Map(location=[lat, lon], zoom_start=10)

In [417]:
ny_map1.choropleth(
    geo_data=filename,
    fill_opacity=0.5, 
    line_opacity=1.0,
    legend_name='Neighborhoods NYC'
)

ny_map_mix.choropleth(
    geo_data=filename,
    fill_opacity=0.5, 
    line_opacity=1.0,
    legend_name='Neighborhoods NYC'
)
# display map
ny_map1

The Choropleth maps look fine,let's check out our centroid.

In [418]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        popup=label,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(ny_map1)

ny_map1

We can see that with this method our 'neighborhood center' is biased towards more irregular sides.  
Let's persist our points in a different map so we can compare them at a later stage.

In [419]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=1, # define how big you want the circle markers to be
        color='red',
        fill=True,
        popup= "Center type 1 " + label,
        fill_color='red'
    ).add_to(ny_map_mix)

#### 2.2.3.2 Center from the rectangle inscribing the neighborhood 

Let's simplify things and let's get the central point of the rectangle inscribing each neighborhood using the minimum and maximum latitude and longitude as vertices. 

In [420]:
for index, row in neighborhoods_data.iterrows():
    if row[2] == 'Polygon':
        df = pd.DataFrame(row[1]).T
        latitude_min = 0
        latitude_max = 0
        longitude_min = 0
        longitude_max = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.dropna().tolist())
            if latitude_min == 0 or latitude_min > df2.min()[1]:
                latitude_min = df2.min()[1]
            if longitude_min == 0 or longitude_min > df2.min()[0]:
                longitude_min = df2.min()[0]
            if latitude_max == 0 or latitude_max < df2.max()[1]:
                latitude_max = df2.max()[1]
            if longitude_max == 0 or longitude_max < df2.max()[0]:
                longitude_max = df2.max()[0]
                
    elif row[2] == 'MultiPolygon':
        df = pd.DataFrame(row[1])
        latitude_min = 0
        latitude_max = 0
        longitude_min = 0
        longitude_max = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.tolist()).T
            for index3, column3 in df2.iteritems():
                df3 = pd.DataFrame(column3.dropna().tolist())
                if latitude_min == 0 or latitude_min > df3.min()[1]:
                    latitude_min = df3.min()[1]
                if longitude_min == 0 or longitude_min > df3.min()[0]:
                    longitude_min = df3.min()[0]
                if latitude_max == 0 or latitude_max < df3.max()[1]:
                    latitude_max = df3.max()[1]
                if longitude_max == 0 or longitude_max < df3.max()[0]:
                    longitude_max = df3.max()[0]
                            
    neighborhoods_data.loc[index, 'latitude_avg']= (latitude_max + latitude_min) / 2
    neighborhoods_data.loc[index, 'longitude_avg']= (longitude_max + longitude_min) / 2
    
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             1895.0   
        East Concourse-Concourse Village       2225.0   
        Highbridge                             2008.0   
        Hunts Point                            1937.5   
        Melrose South-Mott Haven North         1875.0   

                                                                       geometry.coordinates  \
Borough Neighborhood                                                                          
Bronx   Bedford Park-Fordham North        [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        East Concourse-Concourse Village  [[[-73.909587, 40.842756], [-73.909625, 40.842...   
        Highbridge                        [[[-73.917287, 40.845104], [-73.917507, 40.844...   
        Hunts Point                       [[[-73.88439, 40.822967], [-73.883788, 40.8219...   
        Melrose South-Mott Haven North    [[[-73.901293, 40.820475], [-73.90301, 40.8163...   

                                         geometry.type  latitude_avg  \
Borough Neighborhood                                                   
Bronx   Bedford Park-Fordham North             Polygon     40.868678   
        East Concourse-Concourse Village       Polygon     40.830635   
        Highbridge                             Polygon     40.836774   
        Hunts Point                            Polygon     40.813916   
        Melrose South-Mott Haven North         Polygon     40.818335   

                                          longitude_avg  
Borough Neighborhood                                     
Bronx   Bedford Park-Fordham North           -73.891274  
        East Concourse-Concourse Village     -73.916350  
        Highbridge                           -73.924894  
        Hunts Point                          -73.885600  
        Melrose South-Mott Haven North       -73.913960

Now let's plot our neighborhoods and the new centr to see if they look better this time.

In [421]:
means = neighborhoods_data.mean()
lat = means[1]
lon = means[2] 

In [422]:
open(filename)
# create a plain world map
ny_map2 = folium.Map(location=[lat, lon], zoom_start=10)

In [423]:
ny_map2.choropleth(
    geo_data=filename,
    fill_opacity=0.5, 
    line_opacity=1.0,
    legend_name='Neighborhoods NYC'
)

In [424]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        popup=label,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(ny_map2)

ny_map2

It's probably a step forward but we can try another method so let's add this points as well to the support map that we will use to compare the center with the different methods.

In [425]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=1, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        popup="Center type 2 " + label,
        fill_color='yellow',
    ).add_to(ny_map_mix)

#### 2.2.3.3 Centroid from North - East - South - West most points 

We did remove the bias towards more irregular sides but some point (such as Stapleton-Rosebank) now resides outside the neighbohood itself. We can attempt this one more time with a mixed approach using 4 points for each neighborhoods (the North-East-South-West most) and then avarage them out. This way some point might still end up being outside their neighborhood but we should have a more precise result without one side weighing more than another. 

In [426]:
for index, row in neighborhoods_data.iterrows():
    if row[2] == 'Polygon':
        df = pd.DataFrame(row[1]).T
        latitude_min = 0
        latitude_max = 0
        longitude_min = 0
        longitude_max = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.dropna().tolist())
            if latitude_min == 0 or latitude_min > df2.min()[1]:
                latitude_min = df2.min()[1]
                south_longitude = df2.loc[df2[1] == latitude_min,0].values[0]
            if longitude_min == 0 or longitude_min > df2.min()[0]:
                longitude_min = df2.min()[0]
                west_latitude = df2.loc[df2[0] == longitude_min,1].values[0]
            if latitude_max == 0 or latitude_max < df2.max()[1]:
                latitude_max = df2.max()[1]
                north_longitude = df2.loc[df2[1] == latitude_max,0].values[0]
            if longitude_max == 0 or longitude_max < df2.max()[0]:
                longitude_max = df2.max()[0]
                east_latitude = df2.loc[df2[0] == longitude_max,1].values[0]                
        
    elif row[2] == 'MultiPolygon':
        df = pd.DataFrame(row[1])
        latitude_min = 0
        latitude_max = 0
        longitude_min = 0
        longitude_max = 0
        for index2, column2 in df.iteritems():
            df2 = pd.DataFrame(column2.tolist()).T
            for index3, column3 in df2.iteritems():
                df3 = pd.DataFrame(column3.dropna().tolist())
                if latitude_min == 0 or latitude_min > df3.min()[1]:
                    latitude_min = df3.min()[1]
                    south_longitude = df3.loc[df3[1] == latitude_min,0].values[0]
                if longitude_min == 0 or longitude_min > df3.min()[0]:
                    longitude_min = df3.min()[0]
                    west_latitude = df3.loc[df3[0] == longitude_min,1].values[0]
                if latitude_max == 0 or latitude_max < df3.max()[1]:
                    latitude_max = df3.max()[1]
                    north_longitude = df3.loc[df3[1] == latitude_max,0].values[0]
                if longitude_max == 0 or longitude_max < df3.max()[0]:
                    longitude_max = df3.max()[0]
                    east_latitude = df3.loc[df3[0] == longitude_max,1].values[0]
        
    neighborhoods_data.loc[index, 'latitude_avg']= ((latitude_max + latitude_min + east_latitude + west_latitude) / 4)
    neighborhoods_data.loc[index, 'longitude_avg']= ((longitude_max + longitude_min + north_longitude + south_longitude) / 4)
    
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             1895.0   
        East Concourse-Concourse Village       2225.0   
        Highbridge                             2008.0   
        Hunts Point                            1937.5   
        Melrose South-Mott Haven North         1875.0   

                                                                       geometry.coordinates  \
Borough Neighborhood                                                                          
Bronx   Bedford Park-Fordham North        [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        East Concourse-Concourse Village  [[[-73.909587, 40.842756], [-73.909625, 40.842...   
        Highbridge                        [[[-73.917287, 40.845104], [-73.917507, 40.844...   
        Hunts Point                       [[[-73.88439, 40.822967], [-73.883788, 40.8219...   
        Melrose South-Mott Haven North    [[[-73.901293, 40.820475], [-73.90301, 40.8163...   

                                         geometry.type  latitude_avg  \
Borough Neighborhood                                                   
Bronx   Bedford Park-Fordham North             Polygon     40.867171   
        East Concourse-Concourse Village       Polygon     40.829900   
        Highbridge                             Polygon     40.837168   
        Hunts Point                            Polygon     40.811110   
        Melrose South-Mott Haven North         Polygon     40.818316   

                                          longitude_avg  
Borough Neighborhood                                     
Bronx   Bedford Park-Fordham North           -73.890891  
        East Concourse-Concourse Village     -73.917451  
        Highbridge                           -73.927736  
        Hunts Point                          -73.882411  
        Melrose South-Mott Haven North       -73.912290

In [427]:
means = neighborhoods_data.mean()
lat = means[1]
lon = means[2] 

In [428]:
open(filename)
# create a plain world map
ny_map3 = folium.Map(location=[lat, lon], zoom_start=10)

In [429]:
ny_map3.choropleth(
    geo_data=filename,
    fill_opacity=0.5, 
    line_opacity=1.0,
    legend_name='Neighborhoods NYC'
)

In [430]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        popup=label,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(ny_map3)

ny_map3

Persist our new centers on the comparison map as usual.

In [431]:
for latitude, longitude, label in zip(neighborhoods_data.latitude_avg, neighborhoods_data.longitude_avg, neighborhoods_data.index.get_level_values('Neighborhood')):
    folium.features.CircleMarker(
        [latitude, longitude],
        radius=1, # define how big you want the circle markers to be
        color='white',
        fill=True,
        popup="Center type 3 " + label,
        fill_color='white',
    ).add_to(ny_map_mix)


#### 2.2.3.4 Conclusion on neighborhood center points

Finally let's check the centers side by side.

In [432]:
ny_map_mix

Still not perfect but the last solution (white dots) looks probably better in most cases so we will go along with it.

We can now drop the geometry column and rename the columns with the centers coordinates.

In [433]:
neighborhoods_data.head()

Median rent  \
Borough Neighborhood                                    
Bronx   Bedford Park-Fordham North             1895.0   
        East Concourse-Concourse Village       2225.0   
        Highbridge                             2008.0   
        Hunts Point                            1937.5   
        Melrose South-Mott Haven North         1875.0   

                                                                       geometry.coordinates  \
Borough Neighborhood                                                                          
Bronx   Bedford Park-Fordham North        [[[-73.883625, 40.867258], [-73.886833, 40.865...   
        East Concourse-Concourse Village  [[[-73.909587, 40.842756], [-73.909625, 40.842...   
        Highbridge                        [[[-73.917287, 40.845104], [-73.917507, 40.844...   
        Hunts Point                       [[[-73.88439, 40.822967], [-73.883788, 40.8219...   
        Melrose South-Mott Haven North    [[[-73.901293, 40.820475], [-73.90301, 40.8163...   

                                         geometry.type  latitude_avg  \
Borough Neighborhood                                                   
Bronx   Bedford Park-Fordham North             Polygon     40.867171   
        East Concourse-Concourse Village       Polygon     40.829900   
        Highbridge                             Polygon     40.837168   
        Hunts Point                            Polygon     40.811110   
        Melrose South-Mott Haven North         Polygon     40.818316   

                                          longitude_avg  
Borough Neighborhood                                     
Bronx   Bedford Park-Fordham North           -73.890891  
        East Concourse-Concourse Village     -73.917451  
        Highbridge                           -73.927736  
        Hunts Point                          -73.882411  
        Melrose South-Mott Haven North       -73.912290

In [434]:
neighborhoods_data = neighborhoods_data.drop(['geometry.coordinates', 'geometry.type'], axis = 1, errors = 'ignore').rename({'latitude_avg' : 'Center latitude', 'longitude_avg' : 'Center longitude'}, axis = 1)
neighborhoods_data.head()

Median rent  Center latitude  \
Borough Neighborhood                                                     
Bronx   Bedford Park-Fordham North             1895.0        40.867171   
        East Concourse-Concourse Village       2225.0        40.829900   
        Highbridge                             2008.0        40.837168   
        Hunts Point                            1937.5        40.811110   
        Melrose South-Mott Haven North         1875.0        40.818316   

                                          Center longitude  
Borough Neighborhood                                        
Bronx   Bedford Park-Fordham North              -73.890891  
        East Concourse-Concourse Village        -73.917451  
        Highbridge                              -73.927736  
        Hunts Point                             -73.882411  
        Melrose South-Mott Haven North          -73.912290

Much more neat. Now let's proceed with finding the FourSquare venues in each neighborhood vicinity.

### 2.2.4 Venues

#### 2.2.4.1 Preparing the FourSquare query

Start to create a query for a particular neighborhood and check out the response.

In [563]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
radius = 600
latitude = neighborhoods_data.loc[('Queens', 'Breezy Point-Belle Harbor-Rockaway Park-Broad Channel'), 'Center latitude']
longitude = neighborhoods_data.loc[('Queens', 'Breezy Point-Belle Harbor-Rockaway Park-Broad Channel'), 'Center longitude']
url = f'https://api.foursquare.com/v2/venues/explore?client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&ll={latitude},{longitude}&v={VERSION}&radius={radius}&limit={LIMIT}'
url

'https://api.foursquare.com/v2/venues/explore?client_id=BQSIXUEPIAXWIRQCLORU30OOCRJLMQVI5CRSMJK4SPGQS1AA&client_secret=PYJOM0MYRLG3HELSEPMD15UZYQKVCDPGD2XBHJF2OFTJLAPS&ll=40.576834250000005,-73.879249&v=20180604&radius=600&limit=30'

In [564]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ea0a4cf98205d7478938ba8'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Brooklyn',
  'headerFullLocation': 'Brooklyn',
  'headerLocationGranularity': 'city',
  'totalResults': 0,
  'suggestedBounds': {'ne': {'lat': 40.58223425540001,
    'lng': -73.8721526483172},
   'sw': {'lat': 40.5714342446, 'lng': -73.8863453516828}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': []}]}}

The response is a quite complex json, we can try to navigate it down and apply a json_normalize and work with the resulting df. 

In [476]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [507]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) 
nearby_venues.head()

referralId  reasons.count  \
0  e-0-5578d1fc498efdba911d7b1b-0              0   
1  e-0-55df4787498e8cb6cd7d5575-1              0   
2  e-0-4fb7a862e4b095e4290ec1e0-2              0   
3  e-0-4d3244caeefa8cfa58ee34b3-3              0   
4  e-0-4c453ad4dcd61b8d0e7f7c56-4              0   

                                       reasons.items  \
0  [{'summary': 'This spot is popular', 'type': '...   
1  [{'summary': 'This spot is popular', 'type': '...   
2  [{'summary': 'This spot is popular', 'type': '...   
3  [{'summary': 'This spot is popular', 'type': '...   
4  [{'summary': 'This spot is popular', 'type': '...   

                   venue.id                    venue.name  \
0  5578d1fc498efdba911d7b1b                   High Bridge   
1  55df4787498e8cb6cd7d5575                     Fine Fare   
2  4fb7a862e4b095e4290ec1e0  Yankee Stadium Track & Field   
3  4d3244caeefa8cfa58ee34b3                      Rite Aid   
4  4c453ad4dcd61b8d0e7f7c56                  Mullaly Park   

            venue.location.address  venue.location.lat  venue.location.lng  \
0  Harlem River Dr. & W. 172nd St.           40.842049          -73.927047   
1                        Ogden Ave           40.835736          -73.927793   
2                              NaN           40.833397          -73.931335   
3                   1091 Ogden Ave           40.835608          -73.928108   
4                    Jerome Avenue           40.832920          -73.924331   

   venue.location.distance venue.location.postalCode venue.location.cc  \
0                      546                     10452                US   
1                      159                     10452                US   
2                      517                     10451                US   
3                      176                     10452                US   
4                      553                     10452                US   

  venue.location.city venue.location.state venue.location.country  \
0            New York                   NY          United States   
1               Bronx                   NY          United States   
2               Bronx                   NY          United States   
3               Bronx                   NY          United States   
4               Bronx                   NY          United States   

                     venue.location.formattedAddress  \
0  [Harlem River Dr. & W. 172nd St., New York, NY...   
1  [Ogden Ave (W 166 ST), Bronx, NY 10452, United...   
2                   [Bronx, NY 10451, United States]   
3   [1091 Ogden Ave, Bronx, NY 10452, United States]   
4  [Jerome Avenue (164th to 167th Street), Bronx,...   

                                    venue.categories  venue.photos.count  \
0  [{'id': '4bf58dd8d48988d1df941735', 'name': 'B...                   0   
1  [{'id': '50be8ee891d4fa8dcc7199a7', 'name': 'M...                   0   
2  [{'id': '4bf58dd8d48988d106941735', 'name': 'T...                   0   
3  [{'id': '4bf58dd8d48988d10f951735', 'name': 'P...                   0   
4  [{'id': '4bf58dd8d48988d163941735', 'name': 'P...                   0   

  venue.photos.groups venue.location.crossStreet  \
0                  []                        NaN   
1                  []                   W 166 ST   
2                  []                        NaN   
3                  []                        NaN   
4                  []      164th to 167th Street   

                       venue.location.labeledLatLngs venue.delivery.id  \
0                                                NaN               NaN   
1  [{'label': 'display', 'lat': 40.83573590003396...               NaN   
2  [{'label': 'display', 'lat': 40.83339688020503...               NaN   
3  [{'label': 'display', 'lat': 40.8356081, 'lng'...               NaN   
4  [{'label': 'display', 'lat': 40.83291951037224...               NaN   

  venue.delivery.url venue.delivery.provider.name  \
0                NaN                          NaN   
1                Na

Drop some extra.

In [508]:
nearby_venues =nearby_venues.loc[:, ['venue.name', 'venue.categories', 'venue.location.distance']]
nearby_venues

venue.name  \
0                      High Bridge   
1                        Fine Fare   
2     Yankee Stadium Track & Field   
3                         Rite Aid   
4                     Mullaly Park   
5                    Retro Fitness   
6                   Baskin-Robbins   
7                Bravo Supermarket   
8             Little Caesars Pizza   
9                          Dunkin'   
10      New York Yankees Clubhouse   
11          Bx 13 168 St Ogden Ave   
12                  Domino's Pizza   
13              Justine Restaurant   
14  City Fried Chicken - Bronx, NY   
15            La Fuente Restaurant   
16       Highbridge Rail Yard MNRR   
17                         The Pit   

                                     venue.categories  venue.location.distance  
0   [{'id': '4bf58dd8d48988d1df941735', 'name': 'B...                      546  
1   [{'id': '50be8ee891d4fa8dcc7199a7', 'name': 'M...                      159  
2   [{'id': '4bf58dd8d48988d106941735', 'name': 'T...                      517  
3   [{'id': '4bf58dd8d48988d10f951735', 'name': 'P...                      176  
4   [{'id': '4bf58dd8d48988d163941735', 'name': 'P...                      553  
5   [{'id': '4bf58dd8d48988d176941735', 'name': 'G...                      429  
6   [{'id': '4bf58dd8d48988d1c9941735', 'name': 'I...                      598  
7   [{'id': '4bf58dd8d48988d118951735', 'name': 'G...                      522  
8   [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...                      542  
9   [{'id': '4bf58dd8d48988d148941735', 'name': 'D...                      599  
10  [{'id': '52e81612bcbc57f1066b7a2e', 'name': 'S...                      171  
11  [{'id': '4bf58dd8d48988d1fe931735', 'name': 'B...                      170  
12  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...                      586  
13  [{'id': '4bf58dd8d48988d1be941735', 'name': 'L...                      561  
14  [{'id': '4d4b7105d754a06374d81259', 'name': 'F...                      291  
15  [{'id': '4bf58dd8d48988d150941735', 'name': 'S...                      410  
16  [{'id': '4bf58dd8d48988d129951735', 'name': 'T...                      508  
17  [{'id': '4bf58dd8d48988d167941735', 'name': 'S...                      583

And do some cleaning.

In [509]:
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name categories  distance
0                   High Bridge     Bridge       546
1                     Fine Fare     Market       159
2  Yankee Stadium Track & Field      Track       517
3                      Rite Aid   Pharmacy       176
4                  Mullaly Park       Park       553

In [548]:
g_count = nearby_venues.groupby(['categories']).count().drop('distance', axis = 1)
g_sum = nearby_venues.groupby(['categories']).sum()

g_join = g_count.join(g_sum, on = 'categories').sort_values(by = ['name','distance'], ascending = (False,True))
g_join

name  distance
categories                               
Pizza Place                   2      1128
Market                        1       159
Bus Station                   1       170
Sports Club                   1       171
Pharmacy                      1       176
Food                          1       291
Spanish Restaurant            1       410
Gym                           1       429
Train Station                 1       508
Track                         1       517
Grocery Store                 1       522
Bridge                        1       546
Park                          1       553
Latin American Restaurant     1       561
Skate Park                    1       583
Ice Cream Shop                1       598
Donut Shop                    1       599

High bridge doesn't look like a very active place venues wise. Still we need only few categories so we are gonna rank them by ammount of venues of that category and for those that are equally present we can sort them by distance.  
To avoid penalizing neighborhoods in the suburbs as moving around in those areas by car is probably less impacted by traffic and also, in some cases, our choice of the neighborhood center might have influenced the results of this operation. So we will consider a radious of 600 meters incrementing ite until at least 5 venues are identified in the area and limit the amount of venues to 100.

In [566]:
LIMIT = 100

In [567]:
for index, row in neighborhoods_data.iterrows():
    radius = 600
    count = 5
    #get the coordinates of the neighborhood
    latitude = neighborhoods_data.loc[index, 'Center latitude']
    longitude = neighborhoods_data.loc[index, 'Center longitude']
    #prepare the request
    url = f'https://api.foursquare.com/v2/venues/explore?client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&ll={latitude},{longitude}&v={VERSION}&radius={radius}&limit={LIMIT}'
    #get the result and parsing it
    results = requests.get(url).json()
    #to avoid not having data on some Neighborhoods we expand the radius until we find at least count results    
    while results['response']['totalResults'] < count:
        #prepare the request
        url = f'https://api.foursquare.com/v2/venues/explore?client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&ll={latitude},{longitude}&v={VERSION}&radius={radius}&limit={LIMIT}'
        #get the result and parsing it
        results = requests.get(url).json()
        radius += 100
    
    venues = results['response']['groups'][0]['items']
    #transfer in a df and clean it
    nearby_venues = json_normalize(venues)
    nearby_venues = nearby_venues.loc[:, ['venue.name', 'venue.categories', 'venue.location.distance']]
    nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
    nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]
    #create a df with the count of venues by category name
    g_count = nearby_venues.groupby(['categories']).count().drop('distance', axis = 1)
    #create a df with the sum of distances by category
    g_sum = nearby_venues.groupby(['categories']).sum()
    #join the two sets and order them by descending frequency first and ascending distance later
    g_join = g_count.join(g_sum, on = 'categories').sort_values(by = ['name','distance'], ascending = (False,True))
    #reduce the df to the needed number of elements
    g_join = g_join.head(count)
    for index2, row2 in g_join.iterrows():
        neighborhoods_data.loc[index, index2] = row2[0]
neighborhoods_data

Median rent  \
Borough       Neighborhood                                                      
Bronx         Bedford Park-Fordham North                               1895.0   
              East Concourse-Concourse Village                         2225.0   
              Highbridge                                               2008.0   
              Hunts Point                                              1937.5   
              Melrose South-Mott Haven North                           1875.0   
              Mott Haven-Port Morris                                   2200.0   
              Mount Hope                                               1950.0   
              North Riverdale-Fieldston-Riverdale                      3295.0   
              Norwood                                                  1925.0   
              Pelham Parkway                                           2169.0   
              Schuylerville-Throgs Neck-Edgewater Park                 2200.0   
              Soundview-Castle Hill-Clason Point-Harding Park          2025.0   
              Spuyten Duyvil-Kingsbridge                               2600.0   
              University Heights-Morris Heights                        1995.0   
              Van Cortlandt Village                                    1950.0   
              Van Nest-Morris Park-Westchester Square                  2168.0   
              West Concourse                                           1750.0   
              West Farms-Bronx River                                   2000.0   
              Westchester-Unionport                                    1900.0   
Brooklyn      Bath Beach                                               2200.0   
              Bay Ridge                                                2300.0   
              Bedford                                                  2500.0   
              Bensonhurst East                                         1900.0   
              Bensonhurst West                                         2100.0   
              Borough Park                                             1975.0   
              Brighton Beach                                           2262.5   
              Brooklyn Heights-Cobble Hill                             4834.0   
              Bushwick North                                           2450.0   
              Bushwick South                                           2400.0   
              Canarsie                                                 1937.5   
              Carroll Gardens-Columbia Street-Red Hook                 3585.0   
              Clinton Hill                                             2950.0   
              Crown Heights North                                      2400.0   
              Crown Heights South                                      2497.0   
              Cypress Hills-City Line                                  2000.0   
              DUMBO-Vinegar Hill-Downtown Brooklyn-Boerum Hill         4400.0   
              Dyker Heights                                            1950.0   
              East Flatbush-Farragut                                   2212.0   
              East New York                                            1900.0   
              East New York (Pennsylvania Ave)                         2300.0   
              East Williamsburg                                        3000.0   
              Erasmus                                                  1962.5   
              Flatbush                                                 2250.0   
              Flatlands                                                1925.0   
              Fort Greene                                              4690.0   
              Georgetown-Marine Park-Bergen Beach-Mill Basin           2150.0   
              Gravesend                                                2025.0   
              Greenpoint                                               2900.0   
              Ho

In [568]:
neighborhoods_data.shape

(139, 136)

We finally ghatered all the needed data, the next steps will be calculating the distances from Manhattan, and normalize the datas but these problems are gonna be tackled at a later stage.